In [69]:
import pandas as pd
import numpy as np
import pickle

backbone = pd.read_csv("../../data/external/backbone/Taxon.tsv", sep="\t", on_bad_lines='skip')
# drop species with no canonical name
backbone = backbone[np.logical_not(backbone["canonicalName"].isnull())].set_index("canonicalName")
backbone = backbone[np.logical_not(backbone["kingdom"].isnull())]
backbone = backbone[np.logical_not(backbone["phylum"].isnull())]
backbone = backbone[np.logical_not(backbone["class"].isnull())]
backbone = backbone[np.logical_not(backbone["order"].isnull())]
backbone = backbone[np.logical_not(backbone["family"].isnull())]
backbone = backbone[np.logical_not(backbone["genus"].isnull())]

articles = pd.read_pickle("../../data/processed/european_taxonomic_articles_with_subjects.pkl")

C:\Users\melanie\AppData\Local\Temp\ipykernel_5500\3039798173.py:5: DtypeWarning: Columns (9,10,16,21,22) have mixed types. Specify dtype option on import or set low_memory=False.
  backbone = pd.read_csv("../../data/external/backbone/Taxon.tsv", sep="\t", on_bad_lines='skip')


In [94]:
species_count

{'Petromyzon marinus': 3,
 'Bosmina longirostris': 1,
 'Brachionus plicatilis': 6,
 'Pseudoplatystoma corruscans': 1,
 'Pseudoplatystoma reticulatum': 1,
 'Eriocheir sinensis': 2,
 'Gammarus zaddachi': 1,
 'Theodoxus fluviatilis': 2,
 'Radix peregra': 1,
 'Limnadia lenticularis': 2,
 'Salix alba': 3,
 'Fraxinus angustifolia': 1,
 'Ulmus laevis': 3,
 'Quercus robur': 10,
 'Ulmus angustifolia': 1,
 'Quercus angustifolia': 1,
 'Proterorhinus semilunaris': 3,
 'Balanus balanus': 1,
 'Semibalanus balanoides': 3,
 'Placobdella costata': 2,
 'Typha glauca': 1,
 'Dreissena polymorpha': 5,
 'Sparganium angustifolium': 1,
 'Isoetes lacustris': 2,
 'Pinna nobilis': 1,
 'Moina macrocopa': 1,
 'Ranunculus circinatus': 1,
 'Ranunculus fluitans': 3,
 'Chlidonias leucopterus': 1,
 'Chlidonias niger': 1,
 'Rhynchotalona latens': 2,
 'Gammarus pulex': 5,
 'Salmo trutta': 10,
 'Lamprologus tigripictilis': 1,
 'Phanacis phoenixopodos': 1,
 'Callirhytis rufescens': 1,
 'Andricus quercusramuli': 1,
 'Plagio

In [80]:
# count number of articles per species name
species_count = {}

for subjects in articles["species_subject"]:
    if len(subjects) != 0: 
        for species in subjects:
            if species in species_count:
                species_count[species] += 1
            else:
                species_count[species] = 1

df = pd.DataFrame({"canonicalName" : species_count.keys(), 
                   "numberOfArticles" : species_count.values()}).set_index("canonicalName")
# link counts to taxonomic backbone
output = df.join(backbone[["acceptedNameUsageID", "taxonomicStatus"]])

In [105]:
output = df.join(backbone[["acceptedNameUsageID", "taxonomicStatus"]])

In [106]:
output

numberOfArticles  acceptedNameUsageID  \
canonicalName                                                       
Aa figueroi                                1                  NaN   
Aa lehmannii                               1                  NaN   
Aa lehmannii                               1            9433259.0   
Aa lozanoi                                 1                  NaN   
Aabaarnia siphulicola                      1                  NaN   
...                                      ...                  ...   
Zymoseptoria crescenta                     1                  NaN   
Zymoseptoria tritici                       3                  NaN   
Zyras malaybipunctatus                     1                  NaN   
Zyras malaycompressicornis                 1                  NaN   
Zythiostroma pinastri                      1                  NaN   

                              taxonomicStatus  
canonicalName                                  
Aa figueroi                          accepted  
Aa lehmannii                         accepted  
Aa lehmannii                homotypic synonym  
Aa lozanoi                           accepted  
Aabaarnia siphulicola                     NaN  
...                                       ...  
Zymoseptoria crescenta               accepted  
Zymoseptoria tritici                 accepted  
Zyras malaybipunctatus               accepted  
Zyras malaycompressicornis           accepted  
Zythiostroma pinastri                     NaN  

[51163 rows x 3 columns]

In [119]:
[x for x in output[output["taxonomicStatus"]=="accepted"]["acceptedNameUsageID"] if x==x]

[]

In [110]:
list(output.loc["Aa lehmannii", "taxonomicStatus"])

['accepted', 'homotypic synonym']

In [107]:
backbone[backbone["taxonID"]==9433259]

taxonID                             datasetID  \
canonicalName                                                  
Aa lehmannii   9433259  7ddf754f-d193-4cc9-b351-99906754a03b   

               parentNameUsageID  acceptedNameUsageID  originalNameUsageID  \
canonicalName                                                                
Aa lehmannii           2850872.0                  NaN                  NaN   

                                         scientificName  \
canonicalName                                             
Aa lehmannii   Aa lehmannii Rchb.f. ex Szlach. & Kolan.   

                  scientificNameAuthorship genericName specificEpithet  \
canonicalName                                                            
Aa lehmannii   Rchb.f. ex Szlach. & Kolan.          Aa       lehmannii   

              infraspecificEpithet  ...           namePublishedIn  \
canonicalName                       ...                             
Aa lehmannii                   NaN  ...  Ann. Bot. Fenn. ((2014))   

               taxonomicStatus nomenclaturalStatus taxonRemarks  kingdom  \
canonicalName                                                              
Aa lehmannii          accepted                 NaN          NaN  Plantae   

                     phylum       class        order       family genus  
canonicalName                                                            
Aa lehmannii   Tracheophyta  Liliopsida  Asparagales  Orchidaceae    Aa  

[1 rows x 22 columns]

In [140]:
keep = []

for species_name in set(output.index):
    # if a specific species name is accepted somewhere, remove its other exact string matches
    print(output.loc[species.Index])
    if output.loc[species.Index, "taxonomicStatus"] == output.loc[species.Index, "taxonomicStatus"]:
        if "accepted" in list(output.loc[species.Index, "taxonomicStatus"]):
            keep.append(output[output["taxonomicStatus"]=="accepted"].loc[species.Index])
        
pd.concat(keep)

numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOf

numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOf

numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOf

numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOf

numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOf

...

numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOf

numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOf

numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOf

Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aabaarnia siphulicola, dtype: object
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
Name: Aa

KeyboardInterrupt: 

In [91]:
# propagating counts from synonyms to accepted names
keep = []

for species in output.itertuples():
    # if a specific species name is accepted somewhere, remove its other exact string matches
    if "accepted" in list(output.loc[species.Index, "taxonomicStatus"]):
        keep.append(output[output["taxonomicStatus"=="accepted"]].loc[species.Index])
        
    else:
        

for synonym in output[output["taxonomicStatus"]!="accepted"].itertuples():
    print(output.loc[synonym.Index].index)
    if len(output.loc[synonym.Index]) == 1:
        print("aha!")
        # acceptedNameUsageID points to the accepted taxon ID for a synonym
        accepted_name = backbone[backbone["taxonID"]==synonym.acceptedNameUsageID].index[0]
        nr_articles = output.loc[synonym.Index, "numberOfArticles"]

        if accepted_name in list(output.index):
            # add synonym count to existing accepted name if available
            output.loc[accepted_name, "numberOfArticles"] += nr_articles
            output.drop(synonym.Index)
        else:
            # change synonym name to accepted name if unavailable
            output.rename(index={synonym.index:accepted_name}, inplace=True)
    
    # a synonym is often a synonym for multiple accepted species: 
    # in this case, we can't unambiguously use this name
    else:
        print(output.loc[synonym.Index])
        output.drop(synonym.Index)
        
output = output.join(backbone[["kingdom", "phylum", "class", "order", "family", "genus"]])
output.to_pickle("../../data/processed/article_counts_per_taxon.pkl")
output.to_csv("../../data/processed/article_counts_per_taxon.tsv", sep="\t")

Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                       1
acceptedNameUsageID            9433259.0
taxonomicStatus        homotypic synonym
kingdom                          Plantae
phylum                      Tracheophyta
class                         Liliopsida
order                        Asparagales
family                       Orchidaceae
genus                                 Aa
Name: Aa lehmannii, dtype: object
Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles         1
acceptedNameUsageID    NaN
taxonomicStatus        NaN
kingdom                NaN
phylum                 NaN
class                  NaN
order                  NaN
family                 NaN
genus                  NaN
Name: Aabaarnia siphulicola, dtype: obje

Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                       1
acceptedNameUsageID                  NaN
taxonomicStatus                 doubtful
kingdom                         Animalia
phylum                        Arthropoda
class                          Ostracoda
order                         Podocopida
family                 Trachyleberididae
genus                      Abyssocythere
Name: Abyssocythere squalidentata, dtype: object
Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                  1
acceptedNameUsageID       8197555.0
taxonomicStatus             synonym
kingdom                    Animalia
phylum                     Cnidaria
class                      Anthozoa
order                    Alcyonacea
family          

Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                 1
acceptedNameUsageID      9786282.0
taxonomicStatus            synonym
kingdom                   Animalia
phylum                  Arthropoda
class                      Insecta
order                    Hemiptera
family                  Reduviidae
genus                  Acanthaspis
Name: Acanthaspis subinermis, dtype: object
Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                     1
acceptedNameUsageID          2271208.0
taxonomicStatus                synonym
kingdom                       Animalia
phylum                   Echinodermata
class                       Asteroidea
order                        Valvatida
family                 Acanthasteridae
genus          

Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                       1
acceptedNameUsageID           11075786.0
taxonomicStatus        homotypic synonym
kingdom                          Plantae
phylum                      Tracheophyta
class                         Liliopsida
order                        Asparagales
family                       Orchidaceae
genus                       Echinosepala
Name: Acianthera biseta, dtype: object
Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                     1
acceptedNameUsageID         10740989.0
taxonomicStatus                synonym
kingdom                          Fungi
phylum                      Ascomycota
class                  Sordariomycetes
order                      Hypocreales
famil

Index(['Acteon elongatus', 'Acteon elongatus', 'Acteon elongatus',
       'Acteon elongatus', 'Acteon elongatus', 'Acteon elongatus',
       'Acteon elongatus', 'Acteon elongatus', 'Acteon elongatus'],
      dtype='object', name='canonicalName')
                  numberOfArticles  acceptedNameUsageID      taxonomicStatus  \
canonicalName                                                                  
Acteon elongatus                 1           11206394.0              synonym   
Acteon elongatus                 1           11206394.0              synonym   
Acteon elongatus                 1           11206394.0              synonym   
Acteon elongatus                 1            9616836.0  heterotypic synonym   
Acteon elongatus                 1            9616836.0  heterotypic synonym   
Acteon elongatus                 1            9616836.0  heterotypic synonym   
Acteon elongatus                 1            9483260.0  heterotypic synonym   
Acteon elongatus                 1

...

Index(['Beta procumbens', 'Beta procumbens'], dtype='object', name='canonicalName')
                 numberOfArticles  acceptedNameUsageID      taxonomicStatus  \
canonicalName                                                                 
Beta procumbens                 1            5383919.0    homotypic synonym   
Beta procumbens                 1            5383914.0  heterotypic synonym   

                 kingdom        phylum          class           order  \
canonicalName                                                           
Beta procumbens  Plantae  Tracheophyta  Magnoliopsida  Caryophyllales   
Beta procumbens  Plantae  Tracheophyta  Magnoliopsida  Caryophyllales   

                        family genus  
canonicalName                         
Beta procumbens  Amaranthaceae  Beta  
Beta procumbens  Amaranthaceae  Beta  
Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='ob

Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                       1
acceptedNameUsageID            3133950.0
taxonomicStatus        homotypic synonym
kingdom                          Plantae
phylum                      Tracheophyta
class                      Magnoliopsida
order                          Asterales
family                        Asteraceae
genus                          Coreopsis
Name: Bidens tinctoria, dtype: object
Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                 1
acceptedNameUsageID      1681413.0
taxonomicStatus            synonym
kingdom                   Animalia
phylum                  Arthropoda
class                      Insecta
order                   Orthoptera
family                  Tetrigidae

Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                   1
acceptedNameUsageID        5726488.0
taxonomicStatus              synonym
kingdom                     Animalia
phylum                      Mollusca
class                     Gastropoda
order                  Neogastropoda
family                     Muricidae
genus                       Pagodula
Name: Boreotrophon fraseri, dtype: object
Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                       1
acceptedNameUsageID            2918574.0
taxonomicStatus        homotypic synonym
kingdom                          Plantae
phylum                      Tracheophyta
class                      Magnoliopsida
order                        Gentianales
family                  

Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                1
acceptedNameUsageID     9157088.0
taxonomicStatus           synonym
kingdom                  Animalia
phylum                 Arthropoda
class                     Insecta
order                     Diptera
family                  Sciaridae
genus                    Bradysia
Name: Bradysia seticornis, dtype: object
Index(['numberOfArticles', 'acceptedNameUsageID', 'taxonomicStatus', 'kingdom',
       'phylum', 'class', 'order', 'family', 'genus'],
      dtype='object')
numberOfArticles                1
acceptedNameUsageID     1488512.0
taxonomicStatus           synonym
kingdom                  Animalia
phylum                 Arthropoda
class                     Insecta
order                     Diptera
family                  Sciaridae
genus                    Bradysia
Name: Bradysia snyderi, dtype: ob

KeyboardInterrupt: 